# Maps of the Iberian Peninsula – comparison Xi, Omega recension

Olivier Defaux$^{(1)}$, Gerd Graßhoff$^{(1,2)}$, Mohammad Yeghaneh$^{(2)}$

1: Max-Planck-Institute for the History of Science, Berlin

2: Humboldt University, Berlin

Date: August 2019

Ptolemy's catalogue of localities contains a list of places with their coordinates that enables to draw maps of the Iberian Peninsula. Ptolemy's text came down to us in two versions that are sometimes different regarding the spelling of the toponyms and the values of the coordinates. These versions are usually called "Omega recension" and "Xi recension". Based on the Greek text of Ptolemy's catalogue edited by A. Stückelberger and G. Graßhoff (2006), we will draw Ptolemy's map of the Iberian Peninsula and compare the two transmitted versions of his work.

Documentation related to the functions used in the notebook can be found in *tools.py*.

In [1]:
import numpy as np
import pandas as pd
from pandas.io.json import json_normalize
%load_ext autoreload
%autoreload 2

In [2]:
from bokeh.plotting import figure, output_file, show, ColumnDataSource
from bokeh.io import output_notebook, output_file, save
from bokeh.models import HoverTool, BoxZoomTool, ResetTool, WheelZoomTool
from bokeh.layouts import row, gridplot, layout

In [3]:
pd.set_option('display.max_colwidth', -1)
pd.set_option('max_colwidth', 260)

In [4]:
options = {"compact": True, "bg": "#09a3d5",
           "color": "white", "font": "Source Sans Pro","collapse_phrases":False}

In [5]:
!curl -O https://raw.githubusercontent.com/grasshoff/tools/master/citable.py
!curl -O https://raw.githubusercontent.com/grasshoff/tools/master/tools.py

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100  1969  100  1969    0     0   7876      0 --:--:-- --:--:-- --:--:--  7876
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100 11607  100 11607    0     0  43800      0 --:--:-- --:--:-- --:--:-- 43800


In [6]:
from citable import Citable
from tools import Geography, reformatCoord, reformatIntFrac, flatten_list, Js2Geodf

Loading BokehJS ...

## Resources

### Import resources

We work with the part of Ptolemy's catalogue of localities devoted to the Iberian Peninsula (*Geography* 2.4–6). The Greek text of the two recensions (Omega and Xi) can be loaded as .json files from the open-access platform [Zenodo](https://zenodo.org/record/3377419#.XWZBMXvgouU). The *Citable* object uses the DOI number of the publication to assign files to an instance and downloads the required files to a local ./data subdirectory.

In [7]:
PtoleGeodaten = Citable('10.5281/zenodo.3380078')

All files of the repository are already in the local data folder.


In [8]:
Omega = pd.read_json('./data/OmegaStructure.json',encoding="utf8")
Xi = pd.read_json('./data/XiStructure.json',encoding="utf8")

### Transform the .json files into dataframes

The .json files reproduce Ptolemy's text and structure. In order to work with the coordinates in an efficient way, we will transform the file format to produce a simple dataframe for each recension, thanks to the function *Js2Geodf*.

In [9]:
dfOmega=Js2Geodf(Omega["chapters"][0])
dfXi=Js2Geodf(Xi["chapters"][0])

Sample of the dataframe for the Omega recension:

In [10]:
dfOmega[24:31]

ID  category  \
24  2.04.05.13      city   
25  2.04.06.01       NaN   
26  2.04.06.02      city   
27  2.04.06.03      city   
28  2.04.06.04      city   
29  2.04.06.05      city   
30  2.04.06.06  mountain   

                                                                                      coord  \
24  {'long': {'integer': 'ς', 'fraction': 'δ'}, 'lat': {'integer': 'λς', 'fraction': 'γο'}}   
25                                                                                      NaN   
26   {'long': {'integer': 'ς', 'fraction': 'L'}, 'lat': {'integer': 'λς', 'fraction': 'L'}}   
27  {'long': {'integer': 'ς', 'fraction': 'γο'}, 'lat': {'integer': 'λς', 'fraction': 'γ'}}   
28   {'long': {'integer': 'ζ', 'fraction': 'δ'}, 'lat': {'integer': 'λς', 'fraction': 'ς'}}   
29   {'long': {'integer': 'ζ', 'fraction': 'L'}, 'lat': {'integer': 'λς', 'fraction': 'ς'}}   
30   {'long': {'integer': 'ζ', 'fraction': 'L'}, 'lat': {'integer': 'λς', 'fraction': 'δ'}}   

     people                                 text  \
24  Turduli                                  NaN   
25      NaN  Βαστουλῶν τῶν καλουμένων Ποινῶν   
26  Bastuli                                  NaN   
27  Bastuli                                  NaN   
28  Bastuli                                  NaN   
29  Bastuli                                  NaN   
30  Bastuli                                  NaN   

                                              toponym      type       type_sec  
24                                    Βαίλων πόλις   locality  coast section  
25                                                NaN    people  coast section  
26                                          Μενραλία  locality  coast section  
27                                       Τρανσδούκτα  locality  coast section  
28                                         Βαρβησόλα  locality  coast section  
29                                           Καρτμία  locality  coast section  
30  Κάρπη ὅρος καὶ στήλη τῆς ἐντὸς θαλάσσης   locality  coast section

## Transform Greek numbers to decimal coordinates

### Greek numeral notation

Each latitude and each longitude is composed of two parts: an integer part (a whole number of degrees) and a decimal part (written as a fraction of degrees).
In order to plot the localities, we have to transpose the Greek numeral system used by Ptolemy into a modern format, using decimal. The symbols used by Ptolemy to express the coordinates are Greek letters and a special sign for the fraction 1/2.

In [11]:
gfrac={"":0,"ιβ":1/12,"ς":1/6,"δ":1/4,"γ":1/3,"γιβ":5/12,"L":1/2,"Lιβ":7/12,"γο":2/3,"Lδ":3/4,"Lγ":5/6,"Lγιβ":11/12,"η":1/8,"Lς":2/3,"ςL":2/3}
gint={"":0,"α":1,"β":2,"γ":3,"δ":4,"ε":5,"ς":6,"ζ":7,"η":8,"θ":9,"ι":10,"κ":20,"λ":30,"μ":40}

In [12]:
pd.DataFrame(list(gint.items()), columns=['Greek', 'Integers']).sort_values('Integers').set_index('Greek').T

Greek        α  β  γ  δ  ε  ς  ζ  η  θ   ι   κ   λ   μ
Integers  0  1  2  3  4  5  6  7  8  9  10  20  30  40

In [13]:
pd.DataFrame(list(gfrac.items()), columns=['Greek', 'Decimal']).sort_values('Decimal').set_index('Greek').T

Greek               ιβ      η         ς     δ         γ       γιβ    L  \
Decimal  0.0  0.083333  0.125  0.166667  0.25  0.333333  0.416667  0.5   

Greek         Lιβ        γο        Lς        ςL    Lδ        Lγ      Lγιβ  
Decimal  0.583333  0.666667  0.666667  0.666667  0.75  0.833333  0.916667

### Translate into modern numeral notation

We create two columns for each dataframe: one for the longitude, one for the latitude, thanks to the functions *reformatCoord* and *reformatIntFrac*.

- Omega recension

In [14]:
dfTemp = dfOmega.copy()
dfTemp['longitude'] = dfOmega.apply(lambda row: reformatCoord(row,'long','coord'),axis=1).apply(reformatIntFrac)
dfTemp['latitude'] = dfOmega.apply(lambda row: reformatCoord(row,'lat','coord'),axis=1).apply(reformatIntFrac)

The column *coord* contains the parts of the coordinates written with Greek letters; the columns *longitude* and *latitude* contain the coordinates transposed in decimal notation. For instance:

In [15]:
dfTemp.loc[[26]][['toponym','coord','longitude','latitude']]

toponym  \
26  Μενραλία   

                                                                                     coord  \
26  {'long': {'integer': 'ς', 'fraction': 'L'}, 'lat': {'integer': 'λς', 'fraction': 'L'}}   

    longitude  latitude  
26        6.5      36.5

- Xi recension

In [16]:
dfTempX = dfXi.copy()
dfTempX['longitude'] = dfXi.apply(lambda row: reformatCoord(row,'long','coord'),axis=1).apply(reformatIntFrac)
dfTempX['latitude'] = dfXi.apply(lambda row: reformatCoord(row,'lat','coord'),axis=1).apply(reformatIntFrac)

In [17]:
# Sample of the dataframe for the Xi recension:
dfTempX[26:31]

ID  category  \
26  2.04.06.02      city   
27  2.04.06.03      city   
28  2.04.06.04      city   
29  2.04.06.05      city   
30  2.04.06.06  mountain   

                                                                                       coord  \
26    {'long': {'integer': 'ς', 'fraction': 'L'}, 'lat': {'integer': 'λς', 'fraction': 'ς'}}   
27  {'long': {'integer': 'ς', 'fraction': 'Lγ'}, 'lat': {'integer': 'λς', 'fraction': 'ιβ'}}   
28    {'long': {'integer': 'ζ', 'fraction': 'δ'}, 'lat': {'integer': 'λς', 'fraction': 'L'}}   
29    {'long': {'integer': 'ζ', 'fraction': 'L'}, 'lat': {'integer': 'λς', 'fraction': 'ς'}}   
30    {'long': {'integer': 'ζ', 'fraction': 'L'}, 'lat': {'integer': 'λς', 'fraction': 'δ'}}   

     people text                                            toponym      type  \
26  Bastuli  NaN                                          Μενραλία  locality   
27  Bastuli  NaN                                       Τρανζδούκτα  locality   
28  Bastuli  NaN                                  Βαρβησόλα πόλισ  locality   
29  Bastuli  NaN                                           Καρτηία  locality   
30  Bastuli  NaN  Κάλπη ὅρος καὶ στήλη τῆς ἐντὸς θαλάσσης   locality   

         type_sec  longitude   latitude  
26  coast section   6.500000  36.166667  
27  coast section   6.833333  36.083333  
28  coast section   7.250000  36.500000  
29  coast section   7.500000  36.166667  
30  coast section   7.500000  36.250000

We save the dataframes as a dictionary for later use.

In [18]:
df_dict={"dfTemp" : dfTemp,  "dfTempX" : dfTempX}

## Data preparation for the map drawing

Ptolemy's catalogue of localities is composed of localities with different cartographical functions. Coastal localities are meant to be connected in order to let the shape of the continents appears. Inland localities and islands are plotted as individual points on the map. Boundary lines and points enable to draw the shape of the provinces. We need to select in Polemy's catalogue the different sets of localities to produce the maps, with the two recensions of the *Geography*.

### Coasts of the peninsula (Omega)

We select the localities that form the coasts of the peninsula and sort them in the correct order.

In [19]:
dfOmegaCoasts = dfTemp[(dfTemp.type_sec == 'coast section') & (dfTemp.type == 'locality')]
dfOmegaCoasts = dfOmegaCoasts[dfOmegaCoasts.category.apply(lambda row: row not in ['river path','river source'])]

We sort the localities in the correct order.

In [20]:
dfOmegaCoasts = pd.concat([dfOmegaCoasts[39:70].sort_index(ascending=False),dfOmegaCoasts[29:38].sort_index(ascending=False),dfOmegaCoasts[:2],dfOmegaCoasts[4:29],dfTemp[(dfTemp.ID == '2.04.08.08')],dfOmegaCoasts[3:4],dfOmegaCoasts[70:99]])

### Inland boundary lines (Omega)

Ptolemy's map of the Iberian peninsula contains several boundary lines between the provinces that we want to draw.

In [21]:
# boundaries of the Baetica province
boundary_om1 = dfTemp[(dfTemp.ID == '2.04.03.01')].append(dfTemp[(dfTemp.ID == '2.04.03.03')]).append(dfTemp[(dfTemp.ID == '2.04.03.04')]).append(dfTemp[(dfTemp.ID == '2.04.03.07')])

#boundaries of the Lusitania province
boundary_om2 = dfTemp[(dfTemp.ID == '2.05.01.04')].append(dfTemp[(dfTemp.ID == '2.05.01.06')]).append(dfTemp[(dfTemp.ID == '2.05.04.05')]).append(dfTemp[(dfTemp.ID == '2.04.03.04')])

The Pyrenees are defined by four points: three are defined by Ptolemy in the catalogue of the Iberian localities, one is defined in the chapter devoted to the province of Gallia Aquitania.

In [22]:
boundary_om3 = pd.DataFrame({'longitude':[15,17,19,20.333], 'latitude':[45.833,43,43.167,42.333]}).values

### Dictionary for coastlines and boundaries (Omega)

We save the data for the coastline and boundaries as a dictionary for later use.

In [23]:
OmegaCoasts = dfOmegaCoasts[['longitude','latitude']].values
boundary_om1 = boundary_om1[['longitude','latitude']].values
boundary_om2 = boundary_om2[['longitude','latitude']].values

In [24]:
ob_dict={"OmegaCoasts":OmegaCoasts,'boundary_om1' : boundary_om1, 'boundary_om2' : boundary_om2, "boundary_om3":boundary_om3 }

### Coasts of the peninsula (Xi)

In [25]:
dfXiCoasts = dfTempX[(dfTempX.type_sec == 'coast section') & (dfTempX.type == 'locality')]
dfXiCoasts = dfXiCoasts[dfXiCoasts.category.apply(lambda row: row not in ['river path','river source'])]

In [26]:
dfXiCoasts = pd.concat([dfXiCoasts[37:68].sort_index(ascending=False),dfXiCoasts[27:36].sort_index(ascending=False),dfXiCoasts[:2],dfXiCoasts[4:27],dfTempX[(dfTempX.ID == '2.04.08.08')],dfXiCoasts[3:4],dfXiCoasts[70:99]]);

### Inland boundary lines (Xi)

In [27]:
# boundaries of the Baetica province
boundary_xi1 = dfTempX[(dfTempX.ID == '2.04.03.01')].append(dfTempX[(dfTempX.ID == '2.04.03.03')]).append(dfTempX[(dfTempX.ID == '2.04.03.04')]).append(dfTempX[(dfTempX.ID == '2.04.03.07')])

#boundaries of the Lusitania province
boundary_xi2 = dfTempX[(dfTempX.ID == '2.05.01.04')].append(dfTempX[(dfTempX.ID == '2.05.01.06')]).append(dfTempX[(dfTempX.ID == '2.05.04.05')]).append(dfTempX[(dfTempX.ID == '2.04.03.04')])

In [28]:
boundary_xi3 = pd.DataFrame({'longitude':[15.167,17,19,20.333], 'latitude':[45.833,43,43.167,42.333]}).values

### Dictionary for coastlines and boundaries (Xi)

In [29]:
XiCoasts = dfXiCoasts[['longitude','latitude']].values
boundary_xi1 = boundary_xi1[['longitude','latitude']].values
boundary_xi2 = boundary_xi2[['longitude','latitude']].values

In [30]:
xb_dict={'XiCoasts':XiCoasts, 'boundary_xi1' : boundary_xi1, 'boundary_xi2' : boundary_xi2, 'boundary_xi3' : boundary_xi3}

## Maps of the Iberian peninsula

We plot the localities and draw the map of the peninsula according to Ptolemy's text. We use a cartographical projection with meridians and parallel circles intersecting at right angles, where one degree on a parallel circle is equivalent to 3/4 of a degree on a meridian, as Ptolemy defined for this map (*Geography* 8.4.1). We use the dictionaries for the coasts and the boundaries that we defined earlier, as well as the complete list of localities in Ptolemy's catalogue for the Iberian peninsula. 

In [31]:
fig=Geography(ob_dict,xb_dict,df_dict)

### Omega recension

In [32]:
fig.plot_recension(ob_dict,xb_dict,df_dict,"Omega")

### Xi recension

In [33]:
fig.plot_recension(ob_dict,xb_dict,df_dict,"Xi")

## Comparison between the two recensions

We visualise the coordinates of the two recensions of the *Geography* on one single map.

In [34]:
fig.plot_recension_all(ob_dict,xb_dict,df_dict)

We visualise the coordinates differences for each locality. Each place is linked with its counterpart in the other recension, so that we can see the distribution and the importance of the differences on the map. The isolated Omega or Xi points indicate a locality missing in one of the recensions.

In [35]:
fig.plot_compare_recension(ob_dict,xb_dict,df_dict)